En primer lugar se chequea qué tarjeta gráfica nos proporciona GoogleColab. Lo ideal sería utilizar una cuenta Pro, sin embargo, si se utiliza una cuenta gratuita, lo ideal es que la gráfica sea una T4 o una P100, el modelo K80 puede colapsar si intentamos obtener más de 2 samples.


In [ ]:
!nvidia-smi -L

GPU 0: Tesla K80 (UUID: GPU-a5c64d5b-178f-ec85-190a-6b22e518cd7c)


Nos conectamos a google drive para acceder a los samples

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


Se prepara el ambiente instalando las dependencias.

In [ ]:
!pip install git+https://github.com/craftmine1000/jukebox-opt.git

  Cloning https://github.com/craftmine1000/jukebox-opt.git to /tmp/pip-req-build-0rdvjqj9
  Running command git clone -q https://github.com/craftmine1000/jukebox-opt.git /tmp/pip-req-build-0rdvjqj9
     |████████████████████████████████| 60 kB 5.5 MB/s 
     |████████████████████████████████| 238 kB 24.6 MB/s 
     |████████████████████████████████| 3.5 MB 44.8 MB/s 
     |████████████████████████████████| 1.6 MB 38.8 MB/s 
     |████████████████████████████████| 2.4 MB 38.9 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 20.2 MB 1.4 MB/s 
  Created wheel for jukebox: filename=jukebox-1.0-py3-none-any.whl size=204812 sha256=7ef68f28090dc1227609423a6000aed3fc11b442a90fdf88d6e270118f3f710c
  Stored in directory: /tmp/pip-ephem-wheel-cache-16nmoutr/wheels/51/84/29/89b70e25b158ee036f2f49f3302ba9b9f9216bbd1be01cd8d7
  Created wheel for fire: filename=fire-0.1.3-py2.py3

In [ ]:
import jukebox
import torch as t
import librosa
import os
from IPython.display import Audio
from jukebox.make_models import make_vqvae, make_prior, MODELS, make_model
from jukebox.hparams import Hyperparams, setup_hparams
from jukebox.sample import sample_single_window, _sample, \
                           sample_partial_window, upsample, \
                           load_prompts
from jukebox.utils.dist_utils import setup_dist_from_mpi
from jukebox.utils.torch_utils import empty_cache
rank, local_rank, device = setup_dist_from_mpi()

Welcome to jukebox-opt, a system ram optimized version of jukebox.
For most notebooks/enviroments this acts as a mostly drop in replacement.

I say mostly because most notebooks/enviroments tend to load the tokens (zs)
onto the gpu when i want them on the cpu to allow for longer songs, my code
will put it back once loaded from a checkpoint, if the song is to longer than normal
when loading it will use too much gpu memory and probably error out later in
generation. To fix this, go through your notebook and change all 'cuda' to 'cpu'
and all .cuda() to .cpu() for the tokens (zs).

Example; change "zs = t.load(blablabla, location='cuda')" to "zs = t.load(blablabla, location='cpu')"
Example; change "zs = [ z.cuda() for z in zs ]" to "zs = [ z.cpu() for z in zs ]"
Example; change "zs[blabla].cuda()" to "zs[blabla].cpu()"


Using cuda True


In [ ]:
model = '1b_lyrics' # o '5b' o '5b_lyrics', sin embargo, 
                    # estos modelos son más costosos computacionalmente
hps = Hyperparams()
hps.sr = 44100
hps.n_samples = 2 if model in ('1b', '1b_lyrics') else 8
# Indicamos el directorio donde guardaremos los samples generados
# en la ubicación deseada en nuestro Google Drive.
hps.name = '/content/gdrive/MyDrive/Romadizo/tranquilo_cut_3'
chunk_size = 16 if model in ('1b', '1b_lyrics') else 32
max_batch_size = 2 if model in ('1b', '1b_lyrics') else 16
hps.levels = 3
hps.hop_fraction = [1,1,.125]

vqvae, *priors = MODELS[model]
vqvae = make_vqvae(setup_hparams(vqvae, dict(sample_length = 1048576)), device)
top_prior = make_prior(setup_hparams(priors[-1], dict()), vqvae, device)

Running  wget -O /root/.cache/jukebox/models/5b/vqvae.pth.tar https://openaipublic.azureedge.net/jukebox/models/5b/vqvae.pth.tar


100%|██████████| 669/669 [00:00<00:00, 43545.57it/s]


Restored from /root/.cache/jukebox/models/5b/vqvae.pth.tar
0: Loading vqvae in eval mode


  0%|          | 0/72 [00:00<?, ?it/s]

Creating cond. autoregress with prior bins [79, 2048], 
dims [384, 6144], 
shift [ 0 79]
input shape 6528
input bins 2127
Self copy is False


100%|██████████| 72/72 [00:08<00:00,  8.30it/s]


Loading artist IDs from /usr/local/lib/python3.7/dist-packages/jukebox/data/ids/v3_artist_ids.txt
Loading artist IDs from /usr/local/lib/python3.7/dist-packages/jukebox/data/ids/v3_genre_ids.txt
Level:2, Cond downsample:None, Raw to tokens:128, Sample length:786432
Running  wget -O /root/.cache/jukebox/models/1b_lyrics/prior_level_2.pth.tar https://openaipublic.azureedge.net/jukebox/models/1b_lyrics/prior_level_2.pth.tar


100%|██████████| 871/871 [00:51<00:00, 16.84it/s]


Restored from /root/.cache/jukebox/models/1b_lyrics/prior_level_2.pth.tar
0: Loading prior in eval mode


In [ ]:
# mode = primed indica que queremos generar nuevos sonidos a partir de uno existente.
mode = 'primed'
codes_file=None
# Especificamos la ruta donde se encuentra el audio .wav para generar los samples.
audio_file = '/content/gdrive/MyDrive/Romadizo/wav_files/Tranquilo_cut3.wav'
# Especificamos el tiempo que durará el sampleo o generación de sonidos.
prompt_length_in_seconds=6

Ejecutamos esta celda para reanudar automáticamente desde el último archivo de punto de control sólo si este existe. 

In [ ]:
if os.path.exists(hps.name):
  # Identifica el menor nivel ya generado y continúa desde ahí.
  for level in [0, 1, 2]:
    data = f"{hps.name}/level_{level}/data.pth.tar"
    if os.path.isfile(data):
      mode = 'upsample'
      codes_file = data
      print('Upsampling from level '+str(level))
      break
print('mode is now '+mode)

mode is now primed


In [ ]:
# Seteamos los hiperparámertros.
sample_hps = Hyperparams(dict(mode=mode, codes_file=codes_file, audio_file=audio_file, prompt_length_in_seconds=prompt_length_in_seconds))

Especificamos la elección de artista, género, letra y duración del sample a generar.



In [ ]:
sample_length_in_seconds = 20         
hps.sample_length = (int(sample_length_in_seconds*hps.sr)//top_prior.raw_to_tokens)*top_prior.raw_to_tokens
assert hps.sample_length >= top_prior.n_ctx*top_prior.raw_to_tokens, f'Please choose a larger sampling rate'

In [ ]:
metas = [dict(artist = "the strokes",
            genre = "pop",
            total_length = hps.sample_length,
            offset = 0,
            lyrics = """
""",
            ),
          ] * hps.n_samples
labels = [None, None, top_prior.labeller.get_batch_labels(metas, 'cuda')]

Opcionalmente se puede modificar la *temperatura*, luego de varias pruebas y experimentos se recomienda `0.98` o `0.99`

In [ ]:
sampling_temperature = .98

lower_batch_size = 16
max_batch_size = 3 if model in ('1b', '1b_lyrics') else 16
lower_level_chunk_size = 32
chunk_size = 16 if model in ('1b', '1b_lyrics') else 32
sampling_kwargs = [dict(temp=.99, fp16=True, max_batch_size=lower_batch_size,
                        chunk_size=lower_level_chunk_size),
                    dict(temp=0.99, fp16=True, max_batch_size=lower_batch_size,
                         chunk_size=lower_level_chunk_size),
                    dict(temp=sampling_temperature, fp16=True, 
                         max_batch_size=max_batch_size, chunk_size=chunk_size)]

Ahora estamos listos para tomar samples generadas por el modelo. Primero generaremos el nivel superior (2), seguido del primer upsampling (nivel 1) y el segundo upsampling (0).

Después de cada nivel, decodificamos a audio sin procesar y guardamos los archivos de audio.  

Esta celda tomará un tiempo aproximadamente de 10 minutos por 20 segundos de sampleo.

In [ ]:
if sample_hps.mode == 'ancestral':
  zs = [t.zeros(hps.n_samples,0,dtype=t.long, device='cpu') for _ in range(len(priors))]
  zs = _sample(zs, labels, sampling_kwargs, [None, None, top_prior], [2], hps)
elif sample_hps.mode == 'upsample':
  assert sample_hps.codes_file is not None
  data = t.load(sample_hps.codes_file, map_location='cpu')
  zs = [z.cpu() for z in data['zs']]
  assert zs[-1].shape[0] == hps.n_samples, f"Expected bs = {hps.n_samples}, got {zs[-1].shape[0]}"
  del data
  print('Falling through to the upsample step later in the notebook.')
elif sample_hps.mode == 'primed':
  assert sample_hps.audio_file is not None
  audio_files = sample_hps.audio_file.split(',')
  duration = (int(sample_hps.prompt_length_in_seconds*hps.sr)//top_prior.raw_to_tokens)*top_prior.raw_to_tokens
  x = load_prompts(audio_files, duration, hps)
  zs = top_prior.encode(x, start_level=0, end_level=len(priors), bs_chunks=x.shape[0])
  zs = _sample(zs, labels, sampling_kwargs, [None, None, top_prior], [2], hps)
else:
  raise ValueError(f'Unknown sample mode {sample_hps.mode}.')

Sampling level 2
Sampling 6144 tokens for [0,6144]. Conditioning on 2067 tokens
Primed sampling 2 samples with temp=0.98, top_k=0, top_p=0.0
154/154 [01:03<00:00,  2.43it/s]
4077/4077 [06:07<00:00, 11.08it/s]
Sampling 6144 tokens for [746,6890]. Conditioning on 5398 tokens
Primed sampling 2 samples with temp=0.98, top_k=0, top_p=0.0
362/362 [02:40<00:00,  2.25it/s]
746/746 [01:10<00:00, 10.64it/s]


Podemos escuchar los resultados del nivel superior (teniendo en cuenta que esto sonará con mucho ruido hasta que hagamos la etapa de upsampling). 

In [ ]:
Audio(f'{hps.name}/level_2/item_0.wav')

Estamos listos con el modelo top_prior, ahora cargamos los upsamplers.

In [ ]:
if True:
  del top_prior
  empty_cache()
  top_prior=None
upsamplers = [make_prior(setup_hparams(prior, dict()), vqvae, 'cpu') for prior in priors[:-1]]
labels[:2] = [prior.labeller.get_batch_labels(metas, 'cuda') for prior in upsamplers]

Conditioning on 1 above level(s)
Checkpointing convs
Checkpointing convs


100%|██████████| 72/72 [00:08<00:00,  8.60it/s]


Loading artist IDs from /usr/local/lib/python3.7/dist-packages/jukebox/data/ids/v2_artist_ids.txt
Loading artist IDs from /usr/local/lib/python3.7/dist-packages/jukebox/data/ids/v2_genre_ids.txt
Level:0, Cond downsample:4, Raw to tokens:8, Sample length:65536
Running  wget -O /root/.cache/jukebox/models/5b/prior_level_0.pth.tar https://openaipublic.azureedge.net/jukebox/models/5b/prior_level_0.pth.tar


100%|██████████| 1005/1005 [01:17<00:00, 12.93it/s]


Restored from /root/.cache/jukebox/models/5b/prior_level_0.pth.tar
0: Loading prior in eval mode
Conditioning on 1 above level(s)
Checkpointing convs
Checkpointing convs


100%|██████████| 72/72 [00:08<00:00,  8.57it/s]


Loading artist IDs from /usr/local/lib/python3.7/dist-packages/jukebox/data/ids/v2_artist_ids.txt
Loading artist IDs from /usr/local/lib/python3.7/dist-packages/jukebox/data/ids/v2_genre_ids.txt
Level:1, Cond downsample:4, Raw to tokens:32, Sample length:262144
Running  wget -O /root/.cache/jukebox/models/5b/prior_level_1.pth.tar https://openaipublic.azureedge.net/jukebox/models/5b/prior_level_1.pth.tar


100%|██████████| 1005/1005 [01:28<00:00, 11.29it/s]


Restored from /root/.cache/jukebox/models/5b/prior_level_1.pth.tar
0: Loading prior in eval mode


In [ ]:
zs = upsample(zs, labels, sampling_kwargs, [*upsamplers, top_prior], hps)

Sampling level 1
hop_fraction 1 detected, enabling speed upsampling
thank me later, -MichaelsLab
-103512 8268 1
Sampling 8192 tokens for [0,8192]. Conditioning on 0 tokens
Ancestral sampling 2 samples with temp=0.99, top_k=0, top_p=0.0
8192/8192 [11:36<00:00, 11.76it/s]
-103512 8268 1
Sampling 8192 tokens for [0,8192]. Conditioning on 0 tokens
Ancestral sampling 2 samples with temp=0.99, top_k=0, top_p=0.0
8192/8192 [11:34<00:00, 11.80it/s]
Sampling level 0
hop_fraction 1 detected, enabling speed upsampling
thank me later, -MichaelsLab
-20832 33072 4
Sampling 8192 tokens for [0,8192]. Conditioning on 0 tokens
Ancestral sampling 8 samples with temp=0.99, top_k=0, top_p=0.0
8192/8192 [21:49<00:00,  6.25it/s]
-20832 33072 4
Sampling 8192 tokens for [0,8192]. Conditioning on 0 tokens
Ancestral sampling 8 samples with temp=0.99, top_k=0, top_p=0.0
8192/8192 [21:50<00:00,  6.25it/s]


Ahora podemos escuchar nuestro audio final.

In [ ]:
Audio(f'{hps.name}/level_0/item_0.wav')

In [ ]:
del upsamplers
empty_cache()

Nota final: este notebook fue basado en el trabajo de SMarioMan y su reciente release del notebook [Interacting with Jukebox](https://colab.research.google.com/drive/1tY-FSFIbQ_Dxw2Xf-OuPznvgZSBKyVz2?usp=sharing)